In [22]:
import torch
import torch.nn as nn
import torch.optim as optim
from torchvision import datasets, transforms
from torch.utils.data import DataLoader
from torch.autograd import Function

class CustomAutogradFunction(Function):
    @staticmethod
    def forward(ctx, input):
        
        # Store input for use in the backward pass
        ctx.save_for_backward(input)
        
        # You can perform your custom operation here if needed
        output = input  # For demonstration, it just passes input as output
        
        return output

    @staticmethod
    def backward(ctx, grad_output):
        # Print information during the backward pass
        print("Backward pass: Gradients shape:", grad_output.shape)
        print("Gradients values:", grad_output)
        
        # Retrieve the input from the forward pass
        input, = ctx.saved_tensors
        
        # You can perform your custom gradient calculation here if needed
        grad_input = grad_output  # For demonstration, it just passes grad_output as grad_input
        
        return grad_input

In [23]:
# Define a simple neural network class
class NeuralNetwork(nn.Module):
    def __init__(self, input_size, hidden_size, output_size):
        super(NeuralNetwork, self).__init__()
        self.fc1 = nn.Linear(input_size, hidden_size)
        
        self.custom_layer = CustomAutogradFunction.apply
        
        self.explainable = [self.fc1.weight.data[:], self.fc1.bias.data[:]]
        
        self.relu = nn.ReLU()
        self.fc2 = nn.Linear(hidden_size, output_size)

    def forward(self, x):
        x = self.fc1(x)
        x = self.custom_layer(x)
        x = self.relu(x)
        x = self.fc2(x)
        return x

In [24]:
# Hyperparameters
input_size = 784  # MNIST images are 28x28 pixels
hidden_size = 128
output_size = 10  # 10 classes (digits 0-9)
learning_rate = 0.001
batch_size = 64
num_epochs = 10

# Load MNIST dataset
transform = transforms.Compose([transforms.ToTensor(), transforms.Normalize((0.5,), (0.5,))])



In [25]:
train_dataset = datasets.MNIST(root='./data', train=True, transform=transform, download=True)
train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)

# Create the model and optimizer
model = NeuralNetwork(input_size, hidden_size, output_size)
optimizer = optim.Adam(model.parameters(), lr=learning_rate)
criterion = nn.CrossEntropyLoss()

In [26]:


# Training Loop
for epoch in range(num_epochs):
    for batch_idx, (data, targets) in enumerate(train_loader):
        data = data.view(-1, 28 * 28)  # Flatten the input
        optimizer.zero_grad()
        outputs = model(data)
        loss = criterion(outputs, targets)
        loss.backward()
        optimizer.step()

print('Training finished.')
torch.save(model, 'numbers.pth')

Backward pass: Gradients shape: torch.Size([64, 128])
Gradients values: tensor([[ 0.0000,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0014],
        [ 0.0009,  0.0000,  0.0000,  ...,  0.0000,  0.0000, -0.0008],
        [-0.0007,  0.0000,  0.0000,  ...,  0.0000,  0.0000, -0.0010],
        ...,
        [ 0.0007,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0013],
        [ 0.0004,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0008],
        [-0.0006,  0.0000,  0.0000,  ...,  0.0000,  0.0000, -0.0009]])
Backward pass: Gradients shape: torch.Size([64, 128])
Gradients values: tensor([[-0.0009,  0.0000,  0.0000,  ...,  0.0000,  0.0000, -0.0005],
        [-0.0010,  0.0000,  0.0000,  ...,  0.0000,  0.0000, -0.0005],
        [ 0.0010,  0.0000,  0.0000,  ...,  0.0000,  0.0000, -0.0007],
        ...,
        [-0.0002,  0.0000,  0.0011,  ...,  0.0000,  0.0000, -0.0005],
        [-0.0008,  0.0000,  0.0000,  ...,  0.0000,  0.0000,  0.0003],
        [ 0.0010,  0.0000,  0.0000,  ...,  0.0000,  0.0000,

Backward pass: Gradients shape: torch.Size([64, 128])
Gradients values: tensor([[ 2.1234e-04,  0.0000e+00, -5.0240e-05,  ...,  0.0000e+00,
          0.0000e+00,  6.3928e-05],
        [-4.1938e-04,  0.0000e+00,  4.6243e-04,  ...,  0.0000e+00,
          0.0000e+00, -2.0381e-04],
        [-2.7041e-04,  0.0000e+00, -7.8475e-04,  ...,  0.0000e+00,
          0.0000e+00, -5.7915e-04],
        ...,
        [ 7.9696e-05,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00, -3.7106e-04],
        [-4.1695e-04,  0.0000e+00,  9.1800e-04,  ...,  0.0000e+00,
          0.0000e+00,  4.8084e-04],
        [ 1.0140e-03,  0.0000e+00, -1.1940e-03,  ...,  0.0000e+00,
          0.0000e+00,  1.5315e-03]])
Backward pass: Gradients shape: torch.Size([64, 128])
Gradients values: tensor([[ 0.0004,  0.0000,  0.0012,  ...,  0.0000,  0.0000,  0.0013],
        [ 0.0007,  0.0000,  0.0012,  ...,  0.0000,  0.0000,  0.0014],
        [-0.0003,  0.0000, -0.0011,  ...,  0.0000,  0.0000, -0.0006],
        ...,
 

Gradients values: tensor([[-5.1363e-04,  0.0000e+00, -2.6300e-04,  ...,  0.0000e+00,
          0.0000e+00, -8.8886e-04],
        [-1.0868e-04,  0.0000e+00, -3.3519e-04,  ...,  0.0000e+00,
          0.0000e+00, -1.9575e-04],
        [ 4.2290e-04,  0.0000e+00, -5.7834e-04,  ...,  0.0000e+00,
          0.0000e+00, -5.2305e-04],
        ...,
        [ 1.9147e-04,  0.0000e+00, -3.9375e-05,  ...,  0.0000e+00,
          0.0000e+00,  5.3709e-05],
        [-1.1530e-03,  0.0000e+00, -5.4956e-04,  ...,  0.0000e+00,
          0.0000e+00, -1.1830e-03],
        [-3.2103e-04,  0.0000e+00,  8.0777e-04,  ...,  0.0000e+00,
          0.0000e+00, -4.7998e-04]])
Backward pass: Gradients shape: torch.Size([64, 128])
Gradients values: tensor([[ 0.0000e+00,  0.0000e+00, -2.8711e-04,  ...,  0.0000e+00,
          0.0000e+00, -4.3959e-04],
        [ 3.6154e-05,  0.0000e+00, -4.5530e-04,  ...,  0.0000e+00,
          0.0000e+00,  3.6938e-05],
        [-1.3586e-03,  0.0000e+00,  8.5886e-04,  ...,  0.0000e+00,
     

Backward pass: Gradients shape: torch.Size([64, 128])
Gradients values: tensor([[ 2.4242e-04,  0.0000e+00,  1.3770e-03,  ...,  0.0000e+00,
          0.0000e+00,  1.1434e-04],
        [-6.0303e-05,  0.0000e+00, -7.1959e-04,  ...,  0.0000e+00,
          0.0000e+00, -7.6331e-05],
        [-7.0914e-04,  0.0000e+00,  4.5822e-04,  ...,  0.0000e+00,
          0.0000e+00, -6.1425e-04],
        ...,
        [ 2.2152e-05,  0.0000e+00, -1.7620e-04,  ...,  0.0000e+00,
          0.0000e+00,  6.4936e-05],
        [ 1.2035e-03,  0.0000e+00, -1.9158e-03,  ...,  0.0000e+00,
          0.0000e+00,  1.4271e-03],
        [-7.2017e-06,  0.0000e+00, -1.0622e-04,  ...,  0.0000e+00,
          0.0000e+00, -2.1846e-05]])
Backward pass: Gradients shape: torch.Size([64, 128])
Gradients values: tensor([[-6.8008e-05,  0.0000e+00, -1.5746e-04,  ...,  0.0000e+00,
          0.0000e+00, -1.1695e-04],
        [-1.5974e-04,  0.0000e+00,  1.9291e-04,  ...,  0.0000e+00,
          0.0000e+00, -9.8559e-05],
        [-5.9228e-

Backward pass: Gradients shape: torch.Size([64, 128])
Gradients values: tensor([[ 1.3925e-04,  0.0000e+00, -1.9156e-03,  ...,  0.0000e+00,
          0.0000e+00, -1.2154e-03],
        [-7.6560e-06,  0.0000e+00, -9.3165e-05,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [ 8.3808e-05,  0.0000e+00, -3.4923e-05,  ...,  0.0000e+00,
          0.0000e+00,  2.6531e-05],
        ...,
        [-7.1247e-06,  0.0000e+00, -6.4882e-05,  ...,  0.0000e+00,
          0.0000e+00, -2.0613e-05],
        [ 2.2057e-04,  0.0000e+00, -1.7410e-05,  ...,  0.0000e+00,
          0.0000e+00,  7.3408e-05],
        [ 2.9212e-04,  0.0000e+00, -1.1746e-03,  ...,  0.0000e+00,
          0.0000e+00,  1.0764e-03]])
Backward pass: Gradients shape: torch.Size([64, 128])
Gradients values: tensor([[-7.1624e-05,  0.0000e+00,  1.5998e-04,  ...,  0.0000e+00,
          0.0000e+00, -1.9661e-04],
        [-2.1810e-05,  0.0000e+00,  6.0181e-04,  ...,  0.0000e+00,
          0.0000e+00, -2.8231e-04],
        [-6.8085e-

...

Backward pass: Gradients shape: torch.Size([64, 128])
Gradients values: tensor([[ 0.0000e+00,  0.0000e+00,  5.4811e-11,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [ 0.0000e+00,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [-8.8269e-10,  0.0000e+00, -1.3301e-09,  ...,  0.0000e+00,
          0.0000e+00, -1.1667e-09],
        ...,
        [ 0.0000e+00,  0.0000e+00, -3.7860e-05,  ...,  0.0000e+00,
          0.0000e+00,  1.4522e-06],
        [ 0.0000e+00,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [ 0.0000e+00,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00]])
Backward pass: Gradients shape: torch.Size([64, 128])
Gradients values: tensor([[-6.2257e-05,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [ 0.0000e+00,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  1.6067e-07],
        [-2.1088e-

Backward pass: Gradients shape: torch.Size([64, 128])
Gradients values: tensor([[ 6.6428e-06,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [ 1.7639e-10,  0.0000e+00, -1.3826e-09,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [ 0.0000e+00,  0.0000e+00,  1.7028e-06,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        ...,
        [-5.3082e-07,  0.0000e+00, -2.2835e-08,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [-1.5687e-05,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  1.0386e-04],
        [-1.5234e-05,  0.0000e+00,  2.7657e-04,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00]])
Backward pass: Gradients shape: torch.Size([64, 128])
Gradients values: tensor([[-8.8199e-05,  0.0000e+00,  1.6428e-03,  ...,  0.0000e+00,
          0.0000e+00,  3.5204e-04],
        [ 0.0000e+00,  0.0000e+00, -1.8720e-06,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [ 0.0000e+

Backward pass: Gradients shape: torch.Size([64, 128])
Gradients values: tensor([[-4.6497e-07,  0.0000e+00, -1.3156e-06,  ...,  0.0000e+00,
          0.0000e+00, -2.4346e-06],
        [-8.5492e-10,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [ 0.0000e+00,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        ...,
        [-5.6472e-08,  0.0000e+00,  8.9711e-07,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [ 6.4453e-06,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [ 0.0000e+00,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00]])
Backward pass: Gradients shape: torch.Size([64, 128])
Gradients values: tensor([[-2.6204e-06,  0.0000e+00,  1.1150e-06,  ...,  0.0000e+00,
          0.0000e+00, -1.2266e-06],
        [-1.3933e-09,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  1.1643e-10],
        [-2.5850e-

Backward pass: Gradients shape: torch.Size([64, 128])
Gradients values: tensor([[ 4.9497e-04,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [ 5.5658e-08,  0.0000e+00, -8.4887e-07,  ...,  0.0000e+00,
          0.0000e+00, -4.7716e-08],
        [ 0.0000e+00,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00, -4.0806e-07],
        ...,
        [ 2.7923e-11,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [-1.5718e-08,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [ 0.0000e+00,  0.0000e+00,  1.1514e-04,  ...,  0.0000e+00,
          0.0000e+00, -2.3997e-05]])
Backward pass: Gradients shape: torch.Size([64, 128])
Gradients values: tensor([[-1.6746e-06,  0.0000e+00,  3.1915e-07,  ...,  0.0000e+00,
          0.0000e+00, -6.2044e-07],
        [ 1.8794e-10,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [ 0.0000e+

Backward pass: Gradients shape: torch.Size([64, 128])
Gradients values: tensor([[ 0.0000e+00,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00, -2.9719e-08],
        [ 1.4300e-04,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [-1.0222e-08,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00, -1.0947e-08],
        ...,
        [ 0.0000e+00,  0.0000e+00, -2.1533e-06,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [-7.0204e-10,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00, -2.9322e-09],
        [ 0.0000e+00,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  7.0149e-07]])
Backward pass: Gradients shape: torch.Size([64, 128])
Gradients values: tensor([[-7.3159e-08,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  4.3085e-07],
        [ 0.0000e+00,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [-1.9633e-

In [15]:
print(model.explainable)

[tensor([[ 2.3839e-02, -5.8466e-03,  5.9758e-03,  ...,  1.7368e-02,
          8.9825e-03,  2.3738e-02],
        [ 3.9045e-02,  1.5037e-02, -1.3869e-04,  ...,  3.9311e-02,
          1.7824e-02,  5.9217e-03],
        [ 8.4408e-03, -5.1010e-04,  2.5691e-02,  ...,  1.4301e-02,
          3.9605e-02,  2.8213e-02],
        ...,
        [ 9.3567e-03,  2.7215e-02,  2.3847e-02,  ..., -1.0386e-02,
          3.9111e-02, -3.2332e-05],
        [-5.5109e-03,  2.2485e-02, -6.0024e-03,  ..., -1.0203e-02,
          1.1226e-03,  4.0364e-02],
        [ 3.8047e-02,  5.5602e-03,  3.1558e-02,  ...,  2.5590e-02,
          4.1677e-02, -6.0021e-03]]), tensor([ 0.0017, -0.0186, -0.0334, -0.0201,  0.0115, -0.0041,  0.0229, -0.0456,
        -0.0130,  0.0087, -0.0133,  0.0084,  0.0027,  0.0115,  0.0151,  0.0367,
         0.0281, -0.0224, -0.0074, -0.0018, -0.0173, -0.0050,  0.0172, -0.0037,
         0.0111,  0.0030,  0.0179,  0.0126,  0.0099,  0.0349, -0.0024, -0.0256,
        -0.0425, -0.0187, -0.0155, -0.0207,  0

In [10]:
print(model.fc1.weight.data[:])

tensor([[ 0.0007, -0.0111, -0.0226,  ..., -0.0528, -0.0509, -0.0127],
        [-0.0060, -0.0219, -0.0113,  ..., -0.0063,  0.0117,  0.0366],
        [-0.0145,  0.0238, -0.0271,  ...,  0.0280,  0.0426, -0.0143],
        ...,
        [ 0.0091, -0.0142,  0.0320,  ...,  0.0352,  0.0364,  0.0087],
        [ 0.0221,  0.0335, -0.0170,  ...,  0.0320, -0.0005,  0.0402],
        [-0.0177,  0.0455,  0.0135,  ...,  0.0097,  0.0263, -0.0220]])
